In [1]:
import calculate_wait_times
import pandas as pd

trips = pd.read_parquet("output/trips_2024.parquet")
trips = trips.sort_values('start_time')

early_bound = "2024-08-27 12:45"
late_bound = "2024-08-28 00:45"

wait_times = calculate_wait_times.generate_wait_times_df(trips, early_bound, late_bound)
wait_times

route_direction                time  wait_time
0     (901 State Fair - Hub, Fairgrounds-bound) 2024-08-27 12:45:00   0.000000
1     (901 State Fair - Hub, Fairgrounds-bound) 2024-08-27 12:46:00   1.000000
2     (901 State Fair - Hub, Fairgrounds-bound) 2024-08-27 12:47:00   2.000000
3     (901 State Fair - Hub, Fairgrounds-bound) 2024-08-27 12:48:00   3.000000
4     (901 State Fair - Hub, Fairgrounds-bound) 2024-08-27 12:49:00   4.000000
...                                         ...                 ...        ...
4325       (909 Destiny USA, Fairgrounds-bound) 2024-08-28 00:41:00   8.983333
4326       (909 Destiny USA, Fairgrounds-bound) 2024-08-28 00:42:00   9.983333
4327       (909 Destiny USA, Fairgrounds-bound) 2024-08-28 00:43:00  10.983333
4328       (909 Destiny USA, Fairgrounds-bound) 2024-08-28 00:44:00  11.983333
4329       (909 Destiny USA, Fairgrounds-bound) 2024-08-28 00:45:00  12.983333

[4330 rows x 3 columns]

In [25]:
from datetime import date, datetime, timedelta

def wait_times_for_date(trips_df, day):
    start_time = datetime(
        year=day.year, 
        month=day.month,
        day=day.day,
        hour=12, # 8:45 AM Eastern
        minute=45,
        )
    end_time = start_time + timedelta(hours=12) # 8:45 PM Eastern
    return calculate_wait_times.generate_wait_times_df(trips_df, start_time, end_time)

def day_range(start_date, end_date):
    cur_date = start_date
    while cur_date <= end_date:
        yield cur_date
        cur_date += timedelta(days=1)

wait_times = pd.concat([wait_times_for_date(trips, fair_date) for fair_date in day_range(date(2024,8,21), date(2024,9,2))])
wait_times

route_direction                time  wait_time
0     (901 State Fair - Hub, Fairgrounds-bound) 2024-08-21 12:45:00   0.000000
1     (901 State Fair - Hub, Fairgrounds-bound) 2024-08-21 12:46:00   1.000000
2     (901 State Fair - Hub, Fairgrounds-bound) 2024-08-21 12:47:00   2.000000
3     (901 State Fair - Hub, Fairgrounds-bound) 2024-08-21 12:48:00   3.000000
4     (901 State Fair - Hub, Fairgrounds-bound) 2024-08-21 12:49:00   4.000000
...                                         ...                 ...        ...
4325       (909 Destiny USA, Fairgrounds-bound) 2024-09-03 00:41:00   5.933333
4326       (909 Destiny USA, Fairgrounds-bound) 2024-09-03 00:42:00   6.933333
4327       (909 Destiny USA, Fairgrounds-bound) 2024-09-03 00:43:00   7.933333
4328       (909 Destiny USA, Fairgrounds-bound) 2024-09-03 00:44:00   8.933333
4329       (909 Destiny USA, Fairgrounds-bound) 2024-09-03 00:45:00   0.983333

[56304 rows x 3 columns]

In [27]:
import plotly.express as px

to_graph = None
to_graph = wait_times.copy()
to_graph["time"] = to_graph["time"].dt.tz_localize('UTC')
to_graph["time"] = to_graph["time"].dt.tz_convert('US/Eastern')

interval = timedelta(hours=1)

rngBreaks=[]

for i in range(1, len(to_graph)):
        last_time = to_graph['time'].iloc[i-1]
        this_time = to_graph['time'].iloc[i]
        if this_time > last_time + interval:
            # print(f"Maybe we need a rangebreak between {last_time} and {this_time}")
            rngBreaks.append( dict( bounds=[last_time, this_time] ) )

fig = px.line(to_graph, render_mode='svg', x="time", y="wait_time", title='Wait Times for State Fair Buses', color='route_direction', labels={'wait_time': 'Time since last bus (minutes)'})
fig.update_xaxes( rangebreaks=rngBreaks) # , range=[xmin_stupid, xmax_stupid], )

# { pattern: 'hour', bounds: [17, 8] }
#fig.update_xaxes(
#    rangebreaks=[dict(bounds=[17, 17], pattern="hour")],
#    range=[xmin_stupid, xmax_stupid],
#)
fig.show()